# Hyperparameter Tuning using HyperDrive

TODO: Import Dependencies. In the cell below, import all the dependencies that you will need to complete the project.

In [1]:
from azureml.core import Workspace, Experiment
from azureml.widgets import RunDetails
import pandas as pd
from azureml.train.sklearn import SKLearn
from azureml.train.hyperdrive.run import PrimaryMetricGoal
from azureml.train.hyperdrive.policy import BanditPolicy
from azureml.train.hyperdrive.sampling import RandomParameterSampling
from azureml.train.hyperdrive.runconfig import HyperDriveConfig
from azureml.train.hyperdrive.parameter_expressions import choice, uniform
from azureml.core import Environment, ScriptRunConfig
import os
import joblib
from azureml.data.dataset_factory import TabularDatasetFactory
from sklearn.model_selection import train_test_split
from azureml.core import Model

## Dataset

TODO: Get data. In the cell below, write code to access the data you will be using in this project. Remember that the dataset needs to be external.

In [2]:
data = TabularDatasetFactory.from_delimited_files(path="https://automlsamplenotebookdata.blob.core.windows.net/automl-sample-notebook-data/bankmarketing_train.csv")
data_pd = data.to_pandas_dataframe().dropna()
data_pd

age          job  marital          education  default housing loan  \
0       57   technician  married        high.school       no      no  yes   
1       55      unknown  married            unknown  unknown     yes   no   
2       33  blue-collar  married           basic.9y       no      no   no   
3       36       admin.  married        high.school       no      no   no   
4       27    housemaid  married        high.school       no     yes   no   
...    ...          ...      ...                ...      ...     ...  ...   
32945   56    housemaid  married           basic.4y       no      no  yes   
32946   37   management  married  university.degree       no      no  yes   
32947   26       admin.   single  university.degree       no      no   no   
32948   31  blue-collar   single           basic.9y       no      no   no   
32949   39    housemaid  married           basic.4y       no      no   no   

         contact month day_of_week  ...  campaign  pdays  previous  \
0       cellular   may         mon  ...         1    999         1   
1      telephone   may         thu  ...         2    999         0   
2       cellular   may         fri  ...         1    999         1   
3      telephone   jun         fri  ...         4    999         0   
4       cellular   jul         fri  ...         2    999         0   
...          ...   ...         ...  ...       ...    ...       ...   
32945   cellular   jul         mon  ...         1    999         0   
32946   cellular   jul         fri  ...         7    999         0   
32947   cellular   may         tue  ...         4    999         1   
32948   cellular   apr         mon  ...         1    999         0   
32949   cellular   aug         thu  ...         1    999         0   

          poutcome emp.var.rate  cons.price.idx  cons.conf.idx  euribor3m  \
0          failure         -1.8          92.893          -46.2      1.299   
1      nonexistent          1.1          93.994          -36.4      4.860   
2          failure         -1.8          92.893          -46.2      1.313   
3      nonexistent          1.4          94.465          -41.8      4.967   
4      nonexistent          1.4          93.918          -42.7      4.963   
...            ...          ...             ...            ...        ...   
32945  nonexistent          1.4          93.918          -42.7      4.960   
32946  nonexistent          1.4          93.918          -42.7      4.957   
32947      failure         -1.8          92.893          -46.2      1.266   
32948  nonexistent         -1.8          93.075          -47.1      1.405   
32949  nonexistent          1.4          93.444          -36.1      4.963   

       nr.employed   y  
0           5099.1  no  
1           5191.0  no  
2           5099.1  no  
3           5228.1  no  
4           5228.1  no  
...            ...  ..  
32945       5228.1  no  
32946       5228.1  no  
32947       5099.1  no  
32948       5099.1  no  
32949       5228.1  no  

[32950 rows x 21 columns]

In [3]:
ws = Workspace.from_config()
experiment_name = 'Hyperparam_experiment'

experiment=Experiment(ws, experiment_name)

## Hyperdrive Configuration

TODO: Explain the model you are using and the reason for chosing the different hyperparameters, termination policy and config settings.

In [4]:
os.getcwd()

'/mnt/batch/tasks/shared/LS_root/mounts/clusters/notebook196055/code'

In [5]:
# Setup environment for your training run
sklearn_env = Environment.from_conda_specification(name='sklearn-env', file_path='conda_dependencies.yml')

In [63]:
# TODO: Create an early termination policy. This is not required if you are using Bayesian sampling.
early_termination_policy = BanditPolicy(slack_factor=0.1)

#TODO: Create the different params that you will be using during training
param_sampling = RandomParameterSampling(parameter_space={'penalty':choice('l1', 'l2', 'elasticnet', 'none'), 'C': uniform(0.2,2)})

#TODO: Create your estimator and hyperdrive config
#estimator is deprecated, so I used ScriptRunConfig instead
#estimator = <your estimator here>
src = ScriptRunConfig(source_directory='/mnt/batch/tasks/shared/LS_root/mounts/clusters/notebook196055/code',
    script='./train.py',
    compute_target='notebook196055'
    ,environment=sklearn_env)

# Create a HyperDriveConfig using the src object, hyperparameter sampler, and policy.
hyperdrive_run_config =HyperDriveConfig(hyperparameter_sampling=param_sampling,primary_metric_name="Accuracy",primary_metric_goal=PrimaryMetricGoal.MAXIMIZE,
policy=early_termination_policy,run_config=src, max_total_runs=5)

DEBUG:azureml.core._experiment_method:Trying to register submit_function submit, on method <class 'azureml.core.script_run_config.ScriptRunConfig'>
DEBUG:azureml.core._experiment_method:Registered submit_function submit, on method <class 'azureml.core.script_run_config.ScriptRunConfig'>


In [64]:
#TODO: Submit your experiment

hyperdrive_run=experiment.submit(hyperdrive_run_config)


DEBUG:azureml.core._experiment_method:Trying to get submit_function for method_class <class 'azureml.train.hyperdrive.runconfig.HyperDriveConfig'>
DEBUG:azureml.core._experiment_method:Retrieved submit_function search for method <class 'azureml.train.hyperdrive.runconfig.HyperDriveConfig'>
DEBUG:azureml.Experiment#Hyperparam_experiment.submit config HyperDriveConfig:[START]
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1806
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resourc

## Run Details

OPTIONAL: Write about the different models trained and their performance. Why do you think some models did better than others?

TODO: In the cell below, use the `RunDetails` widget to show the different experiments.

In [12]:
RunDetails(hyperdrive_run).show()

_HyperDriveWidget(widget_settings={'childWidgetDisplay': 'popup', 'send_telemetry': False, 'log_level': 'INFO'…

## Best Model

TODO: In the cell below, get the best model from the hyperdrive experiments and display all the properties of the model.

In [65]:
#TODO: Save the best model
best_run=hyperdrive_run.get_best_run_by_primary_metric()
#joblib.dump(best_run.id,'hyperparam_best_model.joblib')

DEBUG:azureml.HyperDriveRun#HD_7e90f536-cedb-4403-bc0c-3314162729a9.RunHistoryFacade.MetricsClient.list_metrics-async:True:[START]
DEBUG:azureml._restclient.service_context.WorkerPool:submitting future: _execute_with_base_arguments
DEBUG:azureml.HyperDriveRun#HD_7e90f536-cedb-4403-bc0c-3314162729a9.RunHistoryFacade.MetricsClient.list_metrics:Using basic handler - no exception handling
DEBUG:azureml.HyperDriveRun#HD_7e90f536-cedb-4403-bc0c-3314162729a9.RunHistoryFacade.MetricsClient:ClientBase: Calling list_metrics with url /metric/v2.0/subscriptions/{subscriptionId}/resourceGroups/{resourceGroupName}/providers/Microsoft.MachineLearningServices/workspaces/{workspaceName}/runs/{runId}/list
DEBUG:azureml.HyperDriveRun#HD_7e90f536-cedb-4403-bc0c-3314162729a9.RunHistoryFacade.MetricsClient.list_metrics-async:True:[STOP]
DEBUG:msrest.service_client:Accept header absent and forced to application/json
DEBUG:azureml.HyperDriveRun#HD_7e90f536-cedb-4403-bc0c-3314162729a9.RunHistoryFacade.MetricsC

In [66]:
best_run

DEBUG:azureml.core._docs:<class 'azureml.core.run.Run'> fully qualified type: azureml.core.run.Run


Run(Experiment: Hyperparam_experiment,
Id: HD_7e90f536-cedb-4403-bc0c-3314162729a9_4,
Type: azureml.scriptrun,
Status: Completed)

DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient.get-async:False:[START]
DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient:ClientBase: Calling get with url /history/v1.0/subscriptions/{subscriptionId}/resourceGroups/{resourceGroupName}/providers/Microsoft.MachineLearningServices/workspaces/{workspaceName}/experiments/{experimentName}/runs/{runId}
DEBUG:msrest.service_client:Accept header absent and forced to application/json
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1806
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:urlli

In [62]:
#best_run.upload_file(name='outputs/'+'hyperparam_best_model_upload',path_or_stream='./hyperparam_best_model_upload')
Model.list(ws)

DEBUG:azureml.ModelsClient.list_query-async:True:[START]
DEBUG:azureml._restclient.clientbase.WorkerPool:submitting future: _execute_with_base_arguments
DEBUG:azureml.ModelsClient.list_query:Using basic handler - no exception handling
DEBUG:azureml.ModelsClient:ClientBase: Calling list_query with url /modelmanagement/v1.0/subscriptions/{subscriptionId}/resourceGroups/{resourceGroup}/providers/Microsoft.MachineLearningServices/workspaces/{workspace}/models
DEBUG:azureml.ModelsClient.list_query-async:True:[STOP]
DEBUG:msrest.service_client:Accept header absent and forced to application/json
DEBUG:azureml.ModelsClient.list_query.WaitingTask:[START]
DEBUG:msrest.universal_http.requests:Configuring retry: max_retries=3, backoff_factor=0.8, max_backoff=90
DEBUG:azureml.ModelsClient.list_query.WaitingTask:Awaiter is ApiPagination
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://m

[Model(workspace=Workspace.create(name='quick-starts-ws-196055', subscription_id='48a74bb7-9950-4cc1-9caa-5d50f995cc55', resource_group='aml-quickstarts-196055'), name=hyperparam_best_model, id=hyperparam_best_model:1, version=1, tags={}, properties={})]

DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient.get-async:False:[START]
DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient:ClientBase: Calling get with url /history/v1.0/subscriptions/{subscriptionId}/resourceGroups/{resourceGroupName}/providers/Microsoft.MachineLearningServices/workspaces/{workspaceName}/experiments/{experimentName}/runs/{runId}
DEBUG:msrest.service_client:Accept header absent and forced to application/json
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1800
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:urlli

## Model Deployment

Remember you have to deploy only one of the two models you trained but you still need to register both the models. Perform the steps in the rest of this notebook only if you wish to deploy this model.

TODO: In the cell below, register the model, create an inference config and deploy the model as a web service.

In [67]:
#hyperparam_model=hyperdrive_run.register_model(model_name='hyperparam_best_model',model_path='azureml-logs/hyperparam_best_model.joblib')
hyperparam_model_reg=best_run.register_model(model_name='hyperparam_best_model2',model_path='outputs/logreg_model.pkl')

DEBUG:azureml.Run#HD_7e90f536-cedb-4403-bc0c-3314162729a9_4.RunHistoryFacade.ArtifactsClient:Fetching files for prefix in ExperimentRun, dcid.HD_7e90f536-cedb-4403-bc0c-3314162729a9_4, outputs/logreg_model.pkl
DEBUG:azureml.Run#HD_7e90f536-cedb-4403-bc0c-3314162729a9_4.RunHistoryFacade.ArtifactsClient.list_sas_by_prefix-async:True:[START]
DEBUG:azureml._restclient.service_context.WorkerPool:submitting future: _execute_with_base_arguments
DEBUG:azureml.Run#HD_7e90f536-cedb-4403-bc0c-3314162729a9_4.RunHistoryFacade.ArtifactsClient.list_sas_by_prefix:Using basic handler - no exception handling
DEBUG:azureml.Run#HD_7e90f536-cedb-4403-bc0c-3314162729a9_4.RunHistoryFacade.ArtifactsClient:ClientBase: Calling list_sas_by_prefix with url /artifact/v2.0/subscriptions/{subscriptionId}/resourceGroups/{resourceGroupName}/providers/Microsoft.MachineLearningServices/workspaces/{workspaceName}/artifacts/prefix/contentinfo/{origin}/{container}/{path}
DEBUG:msrest.service_client:Accept header absent and

In [95]:
#os.path.join(os.getenv('AZUREML_MODEL_DIR'),'logreg_model.pkl')
os.getenv('AZUREML_MODEL_DIR')

DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient.get-async:False:[START]
DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient:ClientBase: Calling get with url /history/v1.0/subscriptions/{subscriptionId}/resourceGroups/{resourceGroupName}/providers/Microsoft.MachineLearningServices/workspaces/{workspaceName}/experiments/{experimentName}/runs/{runId}
DEBUG:msrest.service_client:Accept header absent and forced to application/json
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1805
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:urlli

In [35]:
import json
data=json.load(open('data.json'))
data

{'data': [{'age': 17,
   'campaign': 1,
   'cons.conf.idx': -46.2,
   'cons.price.idx': 92.893,
   'contact': 'cellular',
   'day_of_week': 'mon',
   'default': 'no',
   'duration': 971,
   'education': 'university.degree',
   'emp.var.rate': -1.8,
   'euribor3m': 1.299,
   'housing': 'yes',
   'job': 'blue-collar',
   'loan': 'yes',
   'marital': 'married',
   'month': 'may',
   'nr.employed': 5099.1,
   'pdays': 999,
   'poutcome': 'failure',
   'previous': 1},
  {'age': 87,
   'campaign': 1,
   'cons.conf.idx': -46.2,
   'cons.price.idx': 92.893,
   'contact': 'cellular',
   'day_of_week': 'mon',
   'default': 'no',
   'duration': 471,
   'education': 'university.degree',
   'emp.var.rate': -1.8,
   'euribor3m': 1.299,
   'housing': 'yes',
   'job': 'blue-collar',
   'loan': 'yes',
   'marital': 'married',
   'month': 'may',
   'nr.employed': 5099.1,
   'pdays': 999,
   'poutcome': 'failure',
   'previous': 1}]}

In [37]:
model.predict(data)

AttributeError: 'Model' object has no attribute 'predict'

In [38]:
print(os.getenv('azureml-models '))

None


DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient.get-async:False:[START]
DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient:ClientBase: Calling get with url /history/v1.0/subscriptions/{subscriptionId}/resourceGroups/{resourceGroupName}/providers/Microsoft.MachineLearningServices/workspaces/{workspaceName}/experiments/{experimentName}/runs/{runId}
DEBUG:msrest.service_client:Accept header absent and forced to application/json
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1805
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:urlli

In [27]:
print(os.environ)

environ({'LANG': 'C.UTF-8', 'PATH': '/anaconda/envs/azureml_py36/bin/:/usr/local/sbin:/usr/local/bin:/usr/sbin:/usr/bin:/sbin:/bin:/usr/games:/usr/local/games:/snap/bin', 'HOME': '/home/azureuser', 'LOGNAME': 'azureuser', 'USER': 'azureuser', 'SHELL': '/bin/bash', 'INVOCATION_ID': 'fcdd4f827bfe4171b9db4c41b3b6f69f', 'JOURNAL_STREAM': '9:73343', 'MKL_THREADING_LAYER': 'GNU', 'AML_CloudName': 'AzureCloud', 'CI_RESOURCE_GROUP': 'aml-quickstarts-196055', 'CI_WORKSPACE': 'quick-starts-ws-196055', 'CI_NAME': 'notebook196055', 'CI_LOCAL_UBUNTU_USER': 'azureuser', 'MLFLOW_TRACKING_URI': 'azureml://southcentralus.api.azureml.ms/mlflow/v1.0/subscriptions/48a74bb7-9950-4cc1-9caa-5d50f995cc55/resourceGroups/aml-quickstarts-196055/providers/Microsoft.MachineLearningServices/workspaces/quick-starts-ws-196055', 'ENABLE_MLFLOW_AUTOLOG': 'false', 'MSI_ENDPOINT': 'http://127.0.1.1:46808/MSI/auth', 'MSI_SECRET': 'YIvtbBKqy1bqIUoGOhWb', 'MSI_SECRET_JOB': '1wS3HT9jZ6GQPJo3EFkU', 'OBO_ENDPOINT': 'http://127

DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient.get-async:False:[START]
DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient:ClientBase: Calling get with url /history/v1.0/subscriptions/{subscriptionId}/resourceGroups/{resourceGroupName}/providers/Microsoft.MachineLearningServices/workspaces/{workspaceName}/experiments/{experimentName}/runs/{runId}
DEBUG:msrest.service_client:Accept header absent and forced to application/json
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1806
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:urlli

In [69]:
model_1_path=Model.get_model_path(model_name='hyperparam_best_model2')
model_1_path
#model_path=os.path.join(os.getenv('AZUREML_MODEL_DIR'),'hyperparam_best_model')
#model_1=joblib.load('models/hyperparam_best_model')

DEBUG:azureml.core.run:Could not load run context RunEnvironmentException:
	Message: Could not load a submitted run, if outside of an execution context, use experiment.start_logging to initialize an azureml.core.Run.
	InnerException None
	ErrorResponse 
{
    "error": {
        "message": "Could not load a submitted run, if outside of an execution context, use experiment.start_logging to initialize an azureml.core.Run."
    }
}, switching offline: False
DEBUG:azureml.core.run:Could not load the run context and allow_offline set to False
DEBUG:azureml.core.model:RunEnvironmentException: RunEnvironmentException:
	Message: Could not load a submitted run, if outside of an execution context, use experiment.start_logging to initialize an azureml.core.Run.
	InnerException RunEnvironmentException:
	Message: Could not load a submitted run, if outside of an execution context, use experiment.start_logging to initialize an azureml.core.Run.
	InnerException None
	ErrorResponse 
{
    "error": {
   

ModelNotFoundException: ModelNotFoundException:
	Message: Model hyperparam_best_model2 not found in cache at azureml-models or in current working directory /mnt/batch/tasks/shared/LS_root/mounts/clusters/notebook196055/code. For more info, set logging level to DEBUG.
	InnerException None
	ErrorResponse 
{
    "error": {
        "message": "Model hyperparam_best_model2 not found in cache at azureml-models or in current working directory /mnt/batch/tasks/shared/LS_root/mounts/clusters/notebook196055/code. For more info, set logging level to DEBUG."
    }
}

DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient.get-async:False:[START]
DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient:ClientBase: Calling get with url /history/v1.0/subscriptions/{subscriptionId}/resourceGroups/{resourceGroupName}/providers/Microsoft.MachineLearningServices/workspaces/{workspaceName}/experiments/{experimentName}/runs/{runId}
DEBUG:msrest.service_client:Accept header absent and forced to application/json
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1806
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:urlli

In [88]:
model_1

'HD_daaca8e0-23a5-48b6-b749-c4c6257b323c_0'

In [54]:
#model_1.predict(input_data)
hyperparam_model

Model(workspace=Workspace.create(name='quick-starts-ws-195899', subscription_id='cdbe0b43-92a0-4715-838a-f2648cc7ad21', resource_group='aml-quickstarts-195899'), name=hyperparam_best_model, id=hyperparam_best_model:1, version=1, tags={}, properties={})

In [90]:
from azureml.core.model import InferenceConfig

#environment = best_run.get_context().get_environment()
inference_config = InferenceConfig(entry_script='entry_script.py', environment=sklearn_env)

In [74]:
model=ws.models['hyperparam_best_model2']
model

DEBUG:azureml.ModelsClient.list_query-async:True:[START]
DEBUG:azureml._restclient.clientbase.WorkerPool:submitting future: _execute_with_base_arguments
DEBUG:azureml.ModelsClient.list_query:Using basic handler - no exception handling
DEBUG:azureml.ModelsClient:ClientBase: Calling list_query with url /modelmanagement/v1.0/subscriptions/{subscriptionId}/resourceGroups/{resourceGroup}/providers/Microsoft.MachineLearningServices/workspaces/{workspace}/models
DEBUG:azureml.ModelsClient.list_query-async:True:[STOP]
DEBUG:msrest.service_client:Accept header absent and forced to application/json
DEBUG:azureml.ModelsClient.list_query.WaitingTask:[START]
DEBUG:msrest.universal_http.requests:Configuring retry: max_retries=3, backoff_factor=0.8, max_backoff=90
DEBUG:azureml.ModelsClient.list_query.WaitingTask:Awaiter is ApiPagination
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://m

Model(workspace=Workspace.create(name='quick-starts-ws-196055', subscription_id='48a74bb7-9950-4cc1-9caa-5d50f995cc55', resource_group='aml-quickstarts-196055'), name=hyperparam_best_model2, id=hyperparam_best_model2:1, version=1, tags={}, properties={})

In [91]:
service=Model.deploy(ws, 'hyperparam-webservice5',[model], inference_config)
service.wait_for_deployment(show_output=True)

DEBUG:azureml.ArtifactsClient.batch_create_empty_artifacts-async:False:[START]
DEBUG:azureml.ArtifactsClient:ClientBase: Calling batch_create_empty_artifacts with url /artifact/v2.0/subscriptions/{subscriptionId}/resourceGroups/{resourceGroupName}/providers/Microsoft.MachineLearningServices/workspaces/{workspaceName}/artifacts/batch/metadata/{origin}/{container}
DEBUG:msrest.service_client:Accept header absent and forced to application/json
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1806
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:u

Tips: You can try get_logs(): https://aka.ms/debugimage#dockerlog or local deployment: https://aka.ms/debugimage#debug-locally to debug if deployment takes longer than 10 minutes.
Running

DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1806
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1806
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:azureml._restclient.clientbase:ClientBase: Calling get w


2022-05-18 13:41:40+00:00 Creating Container Registry if not exists.
2022-05-18 13:41:40+00:00 Registering the environment.
2022-05-18 13:41:41+00:00 Use the existing image.
2022-05-18 13:41:41+00:00 Generating deployment configuration.
2022-05-18 13:41:42+00:00 Submitting deployment to compute.
2022-05-18 13:41:44+00:00 Checking the status of deployment hyperparam-webservice5.

DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1806
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1806
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:azureml._restclient.clientbase:ClientBase: Calling get w

.
2022-05-18 13:44:19+00:00 Checking the status of inference endpoint hyperparam-webservice5.
Succeeded


DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1806
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1806
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:azureml._restclient.clientbase:ClientBase: Calling get w

ACI service creation operation finished, operation "Succeeded"


TODO: In the cell below, send a request to the web service you deployed to test it.

In [27]:
import requests
import json

# URL for the web service, should be similar to:
# 'http://8530a665-66f3-49c8-a953-b82a2d312917.eastus.azurecontainer.io/score'
scoring_uri = 'http://409a7c3d-dc06-4851-8946-d6ef1f66bee2.southcentralus.azurecontainer.io/score'
# If the service is authenticated, set the key or token
#key = ''

# Two sets of data to score, so we get two results back
data = {"data":
        [
          {
            "age": 17,
            "campaign": 1,
            "cons.conf.idx": -46.2,
            "cons.price.idx": 92.893,
            "contact": "cellular",
            "day_of_week": "mon",
            "default": "no",
            "duration": 971,
            "education": "university.degree",
            "emp.var.rate": -1.8,
            "euribor3m": 1.299,
            "housing": "yes",
            "job": "blue-collar",
            "loan": "yes",
            "marital": "married",
            "month": "may",
            "nr.employed": 5099.1,
            "pdays": 999,
            "poutcome": "failure",
            "previous": 1
          },
          {
            "age": 87,
            "campaign": 1,
            "cons.conf.idx": -46.2,
            "cons.price.idx": 92.893,
            "contact": "cellular",
            "day_of_week": "mon",
            "default": "no",
            "duration": 471,
            "education": "university.degree",
            "emp.var.rate": -1.8,
            "euribor3m": 1.299,
            "housing": "yes",
            "job": "blue-collar",
            "loan": "yes",
            "marital": "married",
            "month": "may",
            "nr.employed": 5099.1,
            "pdays": 999,
            "poutcome": "failure",
            "previous": 1
          },
      ]
    }
# Convert to JSON string
input_data = json.dumps(data)
with open("data.json", "w") as _f:
    _f.write(input_data)

# Set the content type
#headers = {'Content-Type': 'application/json'}
# If authentication is enabled, set the authorization header
#headers['Authorization'] = f'Bearer {key}'

# Make the request and display the response
resp = requests.post(scoring_uri, input_data)#, headers=headers)
print(resp.json())


test is {'data': [{'age': 17, 'campaign': 1, 'cons.conf.idx': -46.2, 'cons.price.idx': 92.893, 'contact': 'cellular', 'day_of_week': 'mon', 'default': 'no', 'duration': 971, 'education': 'university.degree', 'emp.var.rate': -1.8, 'euribor3m': 1.299, 'housing': 'yes', 'job': 'blue-collar', 'loan': 'yes', 'marital': 'married', 'month': 'may', 'nr.employed': 5099.1, 'pdays': 999, 'poutcome': 'failure', 'previous': 1}, {'age': 87, 'campaign': 1, 'cons.conf.idx': -46.2, 'cons.price.idx': 92.893, 'contact': 'cellular', 'day_of_week': 'mon', 'default': 'no', 'duration': 471, 'education': 'university.degree', 'emp.var.rate': -1.8, 'euribor3m': 1.299, 'housing': 'yes', 'job': 'blue-collar', 'loan': 'yes', 'marital': 'married', 'month': 'may', 'nr.employed': 5099.1, 'pdays': 999, 'poutcome': 'failure', 'previous': 1}]}


In [94]:
#model_path = os.path.join(os.getenv('AZUREML_MODEL_DIR'),'logreg_model.pkl')
model_path=Model.get_model_path(model_name='logreg_model.pkl')
model = joblib.load(model_path)

DEBUG:azureml.core.run:Could not load run context RunEnvironmentException:
	Message: Could not load a submitted run, if outside of an execution context, use experiment.start_logging to initialize an azureml.core.Run.
	InnerException None
	ErrorResponse 
{
    "error": {
        "message": "Could not load a submitted run, if outside of an execution context, use experiment.start_logging to initialize an azureml.core.Run."
    }
}, switching offline: False
DEBUG:azureml.core.run:Could not load the run context and allow_offline set to False
DEBUG:azureml.core.model:RunEnvironmentException: RunEnvironmentException:
	Message: Could not load a submitted run, if outside of an execution context, use experiment.start_logging to initialize an azureml.core.Run.
	InnerException RunEnvironmentException:
	Message: Could not load a submitted run, if outside of an execution context, use experiment.start_logging to initialize an azureml.core.Run.
	InnerException None
	ErrorResponse 
{
    "error": {
   

ModelNotFoundException: ModelNotFoundException:
	Message: Model logreg_model.pkl not found in cache at azureml-models or in current working directory /mnt/batch/tasks/shared/LS_root/mounts/clusters/notebook196055/code. For more info, set logging level to DEBUG.
	InnerException None
	ErrorResponse 
{
    "error": {
        "message": "Model logreg_model.pkl not found in cache at azureml-models or in current working directory /mnt/batch/tasks/shared/LS_root/mounts/clusters/notebook196055/code. For more info, set logging level to DEBUG."
    }
}

DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient.get-async:False:[START]
DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient:ClientBase: Calling get with url /history/v1.0/subscriptions/{subscriptionId}/resourceGroups/{resourceGroupName}/providers/Microsoft.MachineLearningServices/workspaces/{workspaceName}/experiments/{experimentName}/runs/{runId}
DEBUG:msrest.service_client:Accept header absent and forced to application/json
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1806
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:urlli

In [92]:
import requests
scoring_uri = service.scoring_uri
resp = requests.post(scoring_uri, input_data)#, headers=headers)
print(resp.json())

DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 52320e02-e3d1-4f00-b8e0-01ed1d6bb624.southcentralus.azurecontainer.io:80
DEBUG:urllib3.connectionpool:http://52320e02-e3d1-4f00-b8e0-01ed1d6bb624.southcentralus.azurecontainer.io:80 "POST /score HTTP/1.1" 200 33


string indices must be integers


DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient.get-async:False:[START]
DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient:ClientBase: Calling get with url /history/v1.0/subscriptions/{subscriptionId}/resourceGroups/{resourceGroupName}/providers/Microsoft.MachineLearningServices/workspaces/{workspaceName}/experiments/{experimentName}/runs/{runId}
DEBUG:msrest.service_client:Accept header absent and forced to application/json
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1806
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:urlli

<Response [200]>

DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient.get-async:False:[START]
DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient:ClientBase: Calling get with url /history/v1.0/subscriptions/{subscriptionId}/resourceGroups/{resourceGroupName}/providers/Microsoft.MachineLearningServices/workspaces/{workspaceName}/experiments/{experimentName}/runs/{runId}
DEBUG:msrest.service_client:Accept header absent and forced to application/json
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1806
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:urlli

In [85]:
import numpy as np
np.array(input_data['data'])

array([{'age': 17, 'campaign': 1, 'cons.conf.idx': -46.2, 'cons.price.idx': 92.893, 'contact': 'cellular', 'day_of_week': 'mon', 'default': 'no', 'duration': 971, 'education': 'university.degree', 'emp.var.rate': -1.8, 'euribor3m': 1.299, 'housing': 'yes', 'job': 'blue-collar', 'loan': 'yes', 'marital': 'married', 'month': 'may', 'nr.employed': 5099.1, 'pdays': 999, 'poutcome': 'failure', 'previous': 1},
       {'age': 87, 'campaign': 1, 'cons.conf.idx': -46.2, 'cons.price.idx': 92.893, 'contact': 'cellular', 'day_of_week': 'mon', 'default': 'no', 'duration': 471, 'education': 'university.degree', 'emp.var.rate': -1.8, 'euribor3m': 1.299, 'housing': 'yes', 'job': 'blue-collar', 'loan': 'yes', 'marital': 'married', 'month': 'may', 'nr.employed': 5099.1, 'pdays': 999, 'poutcome': 'failure', 'previous': 1}],
      dtype=object)

DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient.get-async:False:[START]
DEBUG:azureml.HyperDriveRun#HD_5532a55a-f9af-4197-a48e-45e38cb60cd7.RunHistoryFacade.RunClient:ClientBase: Calling get with url /history/v1.0/subscriptions/{subscriptionId}/resourceGroups/{resourceGroupName}/providers/Microsoft.MachineLearningServices/workspaces/{workspaceName}/experiments/{experimentName}/runs/{runId}
DEBUG:msrest.service_client:Accept header absent and forced to application/json
DEBUG:urllib3.connectionpool:Starting new HTTP connection (1): 127.0.1.1:46808
DEBUG:urllib3.connectionpool:http://127.0.1.1:46808 "GET /MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01 HTTP/1.1" 200 1806
DEBUG:msrestazure.azure_active_directory:MSI: Retrieving a token from http://127.0.1.1:46808/MSI/auth/?resource=https://management.core.windows.net/&api-version=2017-09-01
DEBUG:msrestazure.azure_active_directory:MSI: token retrieved
DEBUG:urlli

In [34]:
test_sample = json.load(open('data.json'))

prediction = service.run(test_sample)

print(prediction)


JSONDecodeError: [Errno Expecting value] name 'requests' is not defined: 0

In [35]:
scoring_uri = 'http://409a7c3d-dc06-4851-8946-d6ef1f66bee2.southcentralus.azurecontainer.io/score'
resp = requests.post(scoring_uri, input_data)#, headers=headers)
print(resp.json())

test is {'data': [{'age': 17, 'campaign': 1, 'cons.conf.idx': -46.2, 'cons.price.idx': 92.893, 'contact': 'cellular', 'day_of_week': 'mon', 'default': 'no', 'duration': 971, 'education': 'university.degree', 'emp.var.rate': -1.8, 'euribor3m': 1.299, 'housing': 'yes', 'job': 'blue-collar', 'loan': 'yes', 'marital': 'married', 'month': 'may', 'nr.employed': 5099.1, 'pdays': 999, 'poutcome': 'failure', 'previous': 1}, {'age': 87, 'campaign': 1, 'cons.conf.idx': -46.2, 'cons.price.idx': 92.893, 'contact': 'cellular', 'day_of_week': 'mon', 'default': 'no', 'duration': 471, 'education': 'university.degree', 'emp.var.rate': -1.8, 'euribor3m': 1.299, 'housing': 'yes', 'job': 'blue-collar', 'loan': 'yes', 'marital': 'married', 'month': 'may', 'nr.employed': 5099.1, 'pdays': 999, 'poutcome': 'failure', 'previous': 1}]}


TODO: In the cell below, print the logs of the web service and delete the service

In [60]:
print(service.get_logs())

2022-05-17T12:05:25,608029910+00:00 - iot-server/run 
2022-05-17T12:05:25,910077407+00:00 - nginx/run 
2022-05-17T12:05:26,013141721+00:00 - gunicorn/run 
Dynamic Python package installation is disabled.
Starting HTTP server
2022-05-17T12:05:26,109487494+00:00 - rsyslog/run 
EdgeHubConnectionString and IOTEDGE_IOTHUBHOSTNAME are not set. Exiting...
2022-05-17T12:05:28,605269847+00:00 - iot-server/finish 1 0
2022-05-17T12:05:28,607632761+00:00 - Exit code 1 is normal. Not restarting iot-server.
Starting gunicorn 20.1.0
Listening at: http://127.0.0.1:31311 (13)
Using worker: sync
worker timeout is set to 300
Booting worker with pid: 38
SPARK_HOME not set. Skipping PySpark Initialization.
Initializing logger
2022-05-17 12:05:48,304 | root | INFO | Starting up app insights client
logging socket was found. logging is available.
logging socket was found. logging is available.
2022-05-17 12:05:48,305 | root | INFO | Starting up request id generator
2022-05-17 12:05:48,305 | root | INFO | Star

In [ ]:
service.delete()

**Submission Checklist**
- I have registered the model.
- I have deployed the model with the best accuracy as a webservice.
- I have tested the webservice by sending a request to the model endpoint.
- I have deleted the webservice and shutdown all the computes that I have used.
- I have taken a screenshot showing the model endpoint as active.
- The project includes a file containing the environment details.

